In [ ]:
!pip -q install git+https://github.com/huggingface/transformers.git
!pip -q install peft
!pip -q install accelerate
!pip -q install sentencepiece
!pip -q install bitsandbytes

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 9.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 114.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.3/40.3 kB 6.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.3/215.3 kB 24.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 65.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.3/104.3 MB 9.6 MB/s eta 0:00:00


In [5]:
from IPython.display import Markdown as md

import transformers
import peft
import accelerate
import bitsandbytes

print(transformers.__version__)
print(peft.__version__)
print(accelerate.__version__)


4.29.0.dev0
0.2.0
0.18.0


In [1]:
import torch
from peft import PeftModel
from transformers import LlamaTokenizer, LlamaForCausalLM

def load_model(base, finetuned):
    tokenizer = LlamaTokenizer.from_pretrained(base)
    tokenizer.pad_token_id = 0
    tokenizer.padding_side = "left"

    model = LlamaForCausalLM.from_pretrained(
        base,
        load_in_8bit=True,
        device_map="auto",
    )
    
    model = PeftModel.from_pretrained(
        model, 
        finetuned,
        device_map={'': 0}
    )
    return model, tokenizer

def get_output_batch(
    model, tokenizer, prompt, generation_config, device='cuda'
):
  encoding = tokenizer(prompt, return_tensors="pt")
  input_ids = encoding["input_ids"].to(device)
  generated_id = model.generate(
      input_ids=input_ids,
      generation_config=generation_config,
      max_new_tokens=256
  )

  decoded = tokenizer.batch_decode(
      generated_id, skip_prompt=True, skip_special_tokens=True
  )
  del input_ids, generated_id
  torch.cuda.empty_cache()
  return decoded[0].split("### Response:")[-1]


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /usr/local/lib/python3.10/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so...


/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: /usr/lib64-nvidia did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('//172.28.0.1'), PosixPath('http'), PosixPath('8013')}
  warn(msg)
/usr/local/lib/python3.10/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('//colab.research.google.com/tun/m/cc483011

### AlpacaGPT4-LoRA 13B (05/01)

In [14]:
from transformers import GenerationConfig

base = "elinas/llama-13b-hf-transformers-4.29"
sft = "LLMs/AlpacaGPT4-LoRA-13B-elina"

genConfig = GenerationConfig(
    temperature=0.95,
    top_p=0.9,
    top_k=50,
    num_beams=1,
    repetition_penalty=1.2,
    max_new_token=4096,
    do_sample=True,
)

In [3]:
model, tokenizer = load_model(base, sft)

Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

In [15]:
prompt = """### Instruction: Compose an engaging travel blog post about a recent trip to Hawaii, highlighting cultural experiences and must-see attractions.

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Warm beaches, lush rainforests, active volcanoes - these are just some of the stunning natural wonders that make up Hawaii's diverse landscape. As one of the most popular vacation destinations in the world, this tropical paradise is packed with exciting activities, amazing scenery, and rich culture waiting to be explored by adventurous travellers looking for an unparalleled getaway experience. So let me take you on my journey through its captivating cities and towns as I share with you all the reasons why Hawaii should definitely top your bucket list!<br /><br />My first stop was Honolulu, the state capital located along Oahu Island. Its bustling streets offer plenty of opportunities for shopping, dining or just strolling around. But what really captured my attention were its beautiful historic sites like the Aloha Tower Marketplace and Kawaiahao Church - both reminders of how Hawaii has evolved from being a humble fishing village into today’s vibrant city. Not far off lies Waikiki Beach, famous not only for its breathtaking views but also for its lively atmosphere where locals mingle together

In [16]:
prompt = """### Instruction: Can you help me write a formal email to a potential business partner proposing a joint venture?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Dear [Name], <br />I hope this message finds you well. I am writing with the intention of sharing an exciting opportunity that we have identified, and I believe may be mutually beneficial for our respective companies - a possible Joint Venture! The idea behind it is simple; combining both expertise in order to grow our client base, expand market share and maximize profitability by collaborating on projects and cross-selling each other's products or services. With the current climate being as competitive as ever, this partnership would allow us to leverage one another’s strengths and offer unrivaled value to customers. Together, we could do so much more than either company could alone.<br /><br />At [Company Name] we are committed to providing top quality service while staying at the forefront of technological innovation within our industry. We pride ourselves on delivering exceptional solutions to meet your specific needs, and always strive towards excellence. Our passionate team brings together years of experience and knowledge into every project we take part in. Likewise, at [Partner Company] , you provide superior customer support along with cutting edge technology which allows us to consistently exceed expectations. By joining forces we

In [17]:
prompt = """### Instruction: Can you help me write a resignation letter to my current employer, while leaving on good terms and expressing gratitude for the opportunities provided?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Dear [Employer's Name], <br />With deep regret, I am writing this letter of notice regarding my decision to leave your company. My last day with will be [Date]. Thank you so much for all that you have done during these past few years. It has been an honor working with such amazing colleagues in an inspiring environment. Your support and guidance throughout my time here has truly helped develop both professionally and personally, and it is now my time to take the next step in life’s journey. Please accept my sincere appreciation for everything learned from our experiences together; they are memories that I will always cherish.<br /><br />I would like to sincerely thank everyone at [Company] who made the experience rewarding and worthwhile. You are an incredible team with high standards and unparalleled professionalism and commitment. Together we achieved great things!<br /><br />Once again, please accept my heartfelt thanks as I continue forward towards new challenges. Wishing you success and continued growth moving into the future.

In [18]:
prompt = """### Instruction: How can you determine if a restaurant is popular among locals or mainly attracts tourists, and why might this information be useful?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />To determine the level of local patronage for restaurants, there are several factors that we could examine. One such factor would be the number of repeat customers, which may give us an indication on whether they have loyal patrons who visit often or not. Another indicator could be to look at online reviews or social media engagement; these will provide more insight into how satisfied people were with their experience in the restaurant as well as how actively it was promoted within the community. Additionally, by looking at the average spend per person (per meal) and the time spent at the restaurant, we get an idea about how popular the place is overall. <br />Furthermore, examining the location and the type of food served provides some additional clues to determining its appeal. For instance, is the cuisine typical of that region's culture? Is it located near public transport hubs? Do locals frequent the area where the restaurant is situated frequently? A combination of all these pieces of data could help one make a good assessment of whether the establishment has a strong local following, or primarily caters towards visitors from out-of-town. This information can be crucial because it helps businesses better understand what kinds of changes they need

In [19]:
prompt = """### Instruction: What are some subtle clues that suggest someone is pretending to understand a topic or conversation when they are actually confused or uninformed?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />Here are some indications of an individual faking understanding about something:<br />1. They struggle with the basics, e.g., asking repeated questions about what seems like simple concepts and terms related to the given subject matter; 2. They rely on vague words such as "cool" or "good", without providing any actual details about their opinion regarding it; 3. Their responses lack contextual relevance and fail to build upon previous discussions in regards to a particular aspect; 4. When asked for examples from real-life scenarios, there is no concrete evidence that shows that they have had prior exposure/ experience; 5. There’s noticeable pauses during conversational gaps, suggesting confusion or being out of depth; 6. In order to fill up these silent spaces, they may provide answers which seem plausible but do not fully address the question posed; 7. The use of irrelevant information or statements that don't connect with anything previously said could be another indicator; 8. Overly simplified explanations or recurring restatement of basic facts might indicate that the person is trying too hard to convince others that they know more than they actually do; 9. Often

In [13]:
prompt = """### Instruction: What are some potential implications of using a single-use plastic bottle versus a reusable bottle on both the environment and human health?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

<br />A single use plastic water bottles create an immense amount of waste that remains in landfills or littered throughout nature for centuries, posing threat to the environment. When they are not disposed properly, these bottled wastes can cause serious damage like polluting freshwater streams and clogging drains which causes flooding during rainy seasons. In fact, 75% of the world's drinkable water is used by industry and agriculture and only 10% goes towards supporting ecosystems and communities while the rest gets consumed as water (for domestic purposes). So when we consume it from disposable plastics we add more burden to our already depleted resources. On top of this, fossil fuels must be burned to make these plastics, further adding to environmental impact.<br /><br />When considering humans, studies have found that there could potentially be risks associated with consuming water out of single-use plastic containers. For instance, Bisphenol A(BPA) - an industrial chemical commonly used in the production of polycarbonate resin based products including certain types of food containers such as plastic water bottles – has been linked to numerous adverse effects in

In [20]:
prompt = """### Instruction: What factors would you consider when designing an inclusive and accessible public transportation system?

### Response:"""

output = get_output_batch(model, tokenizer, prompt, genConfig)
md(output.replace("\n", "<br />"))

 There are multiple aspects that need to be considered in order for a public transportation system to be truly inclusive and accessible. Some of these factors include, but may not limited to the following:- <br />1) Mobility Impairment- It is crucial to ensure there are sufficient facilities such as ramps, wheelchair lifts or elevators available on all modes of public transportation systems (elevated trains/buses, buses with low floors etc.).<br />2) Visual impairments- This includes features such as audible signage which can help visually impaired people navigate their way around without assistance from anyone else; tactile markings used in addition to visual signals and Braille signs also come under this category.<br />3) Hearing disabilities - Transportation systems should employ staff members who have expertise in helping those with hearing disabilities by using alternative methods like American Sign Language, closed caption displays on screens, written text communication channels and so forth.<br />4) Cognitive / intellectual disability- Such passengers must have equal accessibility while travelling through train stations or even at stops along the journey routes by providing clear directions & easy to understand maps and instructions about timetables and connections between